In [1]:
import cv2
import torch
import os
import glob
import time
from tqdm import tqdm
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.patches as patches

In [2]:
def files(directory_path):
    exclude_keywords = ['orange', 'yellow', 'blue', 'large_orange', 'unknown', 'background', 'rf']
    all_files = glob.glob(os.path.join(directory_path, '*'))
    filtered_files = [file for file in all_files if all(keyword not in file for keyword in exclude_keywords)]
    print(f"Files in {directory_path} after filtering count is: {len(filtered_files)}, missed files: {len(all_files)}")
    return filtered_files

def img_files():
    train_files = files(directory_path = '../../yolov5/data/train/images')
    valid_files = files(directory_path = '../../yolov5/data/valid/images')
    test_files = files(directory_path = '../../yolov5/data/test/images')
    total_list = train_files + valid_files + test_files
    print(len(total_list))
    return total_list

def load_model():
    model = torch.hub.load('../../yolov5', 'custom', path='../../train_trainvalid_dist_augment_voc/fine-tuning-background-augment/weights/best.pt', source='local') 
    return model

def empty_df():
    result_df = pd.DataFrame(columns=['xcenter', 'ycenter', 'width', 'height', 'confidence', 'class', 'name', 'area', 'depth_id', 'depth_name', 'image_name'])
    return result_df

In [3]:
total_list = img_files()

Files in ../../yolov5/data/train/images after filtering count is: 8133, missed files: 117043
Files in ../../yolov5/data/valid/images after filtering count is: 3436, missed files: 14987
Files in ../../yolov5/data/test/images after filtering count is: 361, missed files: 646
11930


In [4]:
model = load_model()

YOLOv5 🚀 v7.0-247-g3f02fde Python-3.10.12 torch-2.1.0+cu121 CUDA:0 (Tesla V100-SXM2-16GB, 16151MiB)

Fusing layers... 
Model summary: 276 layers, 35272008 parameters, 0 gradients, 48.9 GFLOPs
Adding AutoShape... 


In [6]:
pd.options.mode.chained_assignment = None
def create_df(model, total_list):
    time_interval = 5
    result_df = empty_df()
    for path in tqdm(total_list):
        print('path:', path)
        img = path
        results = model(img)
        time.sleep(time_interval)
        image = cv2.imread(path)
        df = results.pandas().xywh[0]

        objects = []
        for index, row in df.iterrows():
            objects.append({'class': row['class'], 'x': row['xcenter'], 'y': row['ycenter'], 'w': row['width'], 'h': row['height'], 'conf':  row['confidence'], 'index': index})
        
        reference_point = np.array([image.shape[1] // 2, image.shape[0] // 2])  # Use the center of the image as the reference point
        
        for obj in objects:
            bbox_center = np.array([obj['x'] * image.shape[1] + obj['w'] * image.shape[1] / 2,
                                    obj['y'] * image.shape[0] + obj['h'] * image.shape[0] / 2])
            obj['distance'] = np.linalg.norm(bbox_center - reference_point)
        
        objects.sort(key=lambda x: x['distance'])
        
        threshold_area = 3000.0 
        
        covered_objects = []
        df['area'] = df['width'] * df['height']
        
        close_df = df[df['area'] > threshold_area]
        close_df['depth_id'] = 0
        close_df['depth_name'] = 'close_from_cam'
        
        far_df = df[df['area'] <= threshold_area]
        far_df['depth_id'] = 1
        far_df['depth_name'] = 'far_from_cam'
        
        concat_df = pd.concat([close_df, far_df], axis=0)
        concat_df['image_name'] = os.path.basename(img)

        result_df = pd.concat([result_df, concat_df], axis=0).reset_index(drop=True)
    return result_df

In [7]:
df = create_df(model, total_list)

  0%|                                                                                                                                                                             | 0/11930 [00:00<?, ?it/s]

path: ../../yolov5/data/train/images/gfr_00544_jpg.jpg


/tmp/ipykernel_1804350/3122779101.py:42: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  result_df = pd.concat([result_df, concat_df], axis=0).reset_index(drop=True)
  0%|                                                                                                                                                                  | 1/11930 [00:05<17:36:34,  5.31s/it]

path: ../../yolov5/data/train/images/fsbizkaia_00081_jpg.jpg


  0%|                                                                                                                                                                  | 2/11930 [00:10<17:20:26,  5.23s/it]

...

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 11928/11930 [17:04:56<00:10,  5.12s/it]

path: ../../yolov5/data/test/images/amz_02149.png


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 11929/11930 [17:05:01<00:05,  5.13s/it]

path: ../../yolov5/data/test/images/ff_00354.png


100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 11930/11930 [17:05:06<00:00,  5.16s/it]


In [8]:
pd.set_option('display.max_columns', None)
pd.options.mode.chained_assignment = 'warn'

df.to_csv('roi_distance.csv', sep=',')